# Silver


In [0]:
import pyspark.pandas as ps
from datetime import datetime
from pyspark.sql import functions as F
from pyspark.sql.functions import col, when, udf
from pyspark.sql.types import StringType

In [0]:
container = "ofertas-empleo"
account = spark.conf.get("adls.account.name")

In [0]:
today = datetime.now().strftime("%Y-%m-%d")
# today = "2025-09-04"
bronze_path = f"abfss://{container}@{account}.dfs.core.windows.net/bronze/jobs_{today}/"
df = spark.read.format("delta").load(bronze_path)
df.show(5)

+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+---------------+--------------------+--------------------+-----------------+--------------------+--------------------+
|                 url|               title|        company_name|         company_url|            location|        applications|         salary|         description|    nivel_antiguedad|      tipo_empleo|     funcion_laboral|            sectores|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+---------------+--------------------+--------------------+-----------------+--------------------+--------------------+
|https://es.linked...|Senior Cloud-Firs...|            Glencore|https://ch.linked...|              Málaga|      53 solicitudes|Sin información|Are we the best-k...|          Intermedio| Jornada completa|Tecnología de la ...|             Minería|
|https://es.link

Eliminar duplicados


In [0]:
df = df.dropDuplicates(["url"])

In [0]:
df = df.withColumn("location_clean", F.trim(F.col("location")))

# Separar ciudad si hay coma
df = df.withColumn("ciudad", F.split(F.col("location_clean"), ",").getItem(0))

# Quitar 'y alrededores' de ciudad
df = df.withColumn("ciudad", F.regexp_replace("ciudad", " y alrededores", ""))

# Normalizar espacios y caracteres
df = df.withColumn("ciudad", F.trim(F.col("ciudad")))

df = df.drop("location")

In [0]:
df.select("ciudad").distinct().show(100, truncate=False)


+-------------------------------------------+
|ciudad                                     |
+-------------------------------------------+
|Dos Hermanas                               |
|Málaga                                     |
|Badajoz                                    |
|Elche/Elx                                  |
|Madrid                                     |
|España                                     |
|Pamplona/Iruña                             |
|Castellón de la Plana/Castelló de la Plana |
|Leganés                                    |
|Vitoria-Gasteiz                            |
|Orense                                     |
|Bilbao                                     |
|Murcia                                     |
|Vizcaya                                    |
|Terrassa                                   |
|Pozuelo de Alarcón                         |
|Cornellà de Llobregat                      |
|San Fernando de Henares                    |
|Nava                             

In [0]:
mapping = {
    # Cataluña
    "Barcelona": "Cataluña",
    "Sant Cugat del Vallès": "Cataluña",
    "Tarrasa": "Cataluña",
    "Sabadell": "Cataluña",
    "Cornellà de Llobregat": "Cataluña",
    "Mataró": "Cataluña",
    "Cerdanyola del Vallès": "Cataluña",
    "Barberà del Vallès": "Cataluña",
    "Vallés Occidental": "Cataluña",
    "Montmeló": "Cataluña",

    # Comunidad Valenciana
    "Valencia": "Comunidad Valenciana",
    "Valencia/València": "Comunidad Valenciana",
    "Alicante/Alacant": "Comunidad Valenciana",
    "Castellón de la Plana/Castelló de la Plana": "Comunidad Valenciana",
    "Elche/Elx": "Comunidad Valenciana",
    "Paterna": "Comunidad Valenciana",
    "Albalat dels Sorells": "Comunidad Valenciana",
    "Comunidad Valenciana / Comunitat Valenciana": "Comunidad Valenciana",

    # Comunidad de Madrid
    "Madrid": "Madrid",
    "Pozuelo de Alarcón": "Madrid",
    "Tres Cantos": "Madrid",
    "Leganés": "Madrid",
    "Torrejón de Ardoz": "Madrid",
    "Las Rozas de Madrid": "Madrid",
    "Alcobendas": "Madrid",
    "Rivas-Vaciamadrid": "Madrid",
    "Sevilla La Nueva": "Madrid",

    # Andalucía
    "Sevilla": "Andalucía",
    "Málaga": "Andalucía",
    "Granada": "Andalucía",
    "Córdoba": "Andalucía",
    "Huelva": "Andalucía",
    "Cádiz": "Andalucía",
    "Marbella": "Andalucía",
    "Andalucía": "Andalucía",

    # País Vasco
    "Bilbao": "País Vasco",
    "Vitoria-Gasteiz": "País Vasco",
    "Donostia-San Sebastián": "País Vasco",
    "Zamudio": "País Vasco",
    "Álava": "País Vasco",
    "Alava": "País Vasco",

    # Galicia
    "La Coruña": "Galicia",
    "Vigo": "Galicia",
    "Orense": "Galicia",
    "O Porriño": "Galicia",

    # Asturias
    "Oviedo": "Asturias",
    "Gijón": "Asturias",
    "Mieres": "Asturias",
    "Nava": "Asturias",

    # Castilla y León
    "León": "Castilla y León",
    "Valladolid": "Castilla y León",
    "Salamanca": "Castilla y León",

    # Aragón
    "Zaragoza": "Aragón",

    # Región de Murcia
    "Murcia": "Región de Murcia",
    "Alhama de Murcia": "Región de Murcia",

    # Canarias
    "Las Palmas de Gran Canaria": "Canarias",

    # Baleares
    "Palma": "Islas Baleares",
    "Mahón": "Islas Baleares",

    # Castilla-La Mancha
    "Albacete": "Castilla-La Mancha",

    # Extranjero
    "O Porto": "Portugal",
    "España": "España"  # cuando no hay más detalle
}


def map_comunidad(ciudad):
    return mapping.get(ciudad, "Desconocida")



In [0]:
df.printSchema()


root
 |-- url: string (nullable = true)
 |-- title: string (nullable = true)
 |-- company_name: string (nullable = true)
 |-- company_url: string (nullable = true)
 |-- applications: string (nullable = true)
 |-- salary: string (nullable = true)
 |-- description: string (nullable = true)
 |-- nivel_antiguedad: string (nullable = true)
 |-- tipo_empleo: string (nullable = true)
 |-- funcion_laboral: string (nullable = true)
 |-- sectores: string (nullable = true)
 |-- location_clean: string (nullable = true)
 |-- ciudad: string (nullable = true)



In [0]:
from pyspark.sql import functions as F
from pyspark.sql.functions import col, when, udf
from pyspark.sql.types import StringType

udf_map = udf(map_comunidad, StringType())

df = df.withColumn("Comunidad_Autonoma", udf_map(col("ciudad")))

In [0]:
display(df)

url title company_name company_url applications salary description nivel_antiguedad tipo_empleo funcion_laboral sectores location_clean ciudad Comunidad_Autonoma https://es.linkedin.com/jobs/view/%F0%9F%8C%8D-backend-developer-python-go-aws-100%25-remoto-%F0%9F%8C%8D-at-knowmad-mood-4295589561?position=9&pageNum=2&refId=k6gNPYI%2FL9xDzDB6w%2ByuLA%3D%3D&trackingId=vgXigtttIfXByxfH%2FwFlEw%3D%3D 🌍 Backend Developer Python - GO - AWS (100% remoto) 🌍 knowmad mood https://es.linkedin.com/company/knowmad-mood?trk=public_jobs_topcard-org-name Sé de los primeros 25 solicitantes Sin información Si tienes experiencia como Programador/a GO / Python y además cuentas con experiencia con AWS especialmente en infraestructura como código (Terraform) y quieres trabajar en una empresa del sector farmacéutico, en una modalidad 100% teletrabajo ¡esta es tu oferta!¿Qué ofrecemos?🏡 Posición 100% remota 🏡Horario flexible ⏰Vacaciones 🌴: Disfruta de 22 días de vacaciones más 2 días de libre disposición, además de los días 24 y 31 de diciembre libres = 26 días.Contrato indefinido 📄: Desde el primer día, con la opción de elegir si prefieres recibir tu nómina en 12 o 14 pagas.Retribución flexible 💳: Elige cómo destinar parte de tu salario a productos o servicios con ventajas fiscales, como tarjeta restaurante, cheque guardería, seguro médico o formación.Club de ventajas: Accede a descuentos exclusivos en tecnología, ocio y formación para mejorar tu vida personal.Formación continua 📚: Accede a plataformas como Udemy Business, además de cursos de idiomas, certificaciones oficiales y formación técnica, adaptados a tus necesidades y ritmo.Plan de carrera 🌱: Diseña tu propio camino de crecimiento, con apoyo para avanzar dentro de la empresa, transitar entre comunidades o asumir roles de liderazgo.Bienestar integral 🧘: Acceso a nuestro programa de bienestar que incluye nutrición saludable, actividad física y talleres de equilibrio emocional.Conciliación +VIDA: Asistencia personal y familiar 24/7, con servicios como consultas médicas, legales, dentales, asistencia personal, renovación de carnet de conducir y más para ti y tus familiares.Ambiente de trabajo inclusivo 🌍: Fomentamos la diversidad generacional y cultural, con políticas activas de igualdad y diversidad en un entorno de más de 70 nacionalidades.Eventos sociales y diversión 🎉: Participa en actividades como videojuegos multijugador, escape rooms virtuales y más, para conectar con tus compañeros fuera del entorno laboral.Tu misión en el proyecto:Soporte y Mejora del SistemaPlanificar, diseñar, configurar, implementar, mejorar, actualizar, probar, operar, mantener, asegurar, monitorear, liberar (gestionar cambios y comunicar a las partes interesadas) y documentar el Sistema Informático (solución SaaS + AWS), incluyendo todos sus componentes durante todo su ciclo de vida.Gestionar tareas diarias de soporte, resolución de incidencias y problemas de manera eficiente.Gestión de Infraestructura y Entornos:Apoyar en la provisión de recursos de infraestructura AWS. Diseñar, construir y desplegar configuraciones de servicios AWS usando plantillas Terraform o blueprints para servicios como S3, Lambda, IAM, MWAA, ECS, Glue y RDS.Asegurar que los entornos AWS y OpenShift sean rentables y funcionen de manera óptima. Implementar monitoreo para detectar y responder a eventos/incidencias.Configurar pipelines CI/CD para automatizar la promoción de nuevas versiones a entornos superiores.Gestión de Producto:Colaborar dentro del equipo de producto para facilitar el despliegue del sistema CPM en múltiples mercados.Participar activamente en ceremonias Scrum de gestión ágil de proyectos. Ayudar a los socios comerciales y al equipo a refinar historias de usuario. Especificar y documentar requisitos. Colaborar con equipos globales para asegurar entregas de proyectos a tiempo y dentro del alcance.Requisitos:Mínimo 3-4 años en un puesto similar.Dominio de Python y Go.Fluidez en inglés oral (obligatorio) nivel C1. Además, se tendr

Normalizar el campo de nivel de antiguedad

In [0]:

# Nivel de antigüedad
seniority_map = {
    "Sin experiencia": "Junior",
    "Prácticas": "Intern",
    "Intermedio": "Mid",
    "Algo de responsabilidad": "Mid",
    "Director": "Senior",
    "Ejecutivo": "Senior",
    "No corresponde": None
}


# Aplicar mapeo en PySpark
seniority_udf = F.udf(lambda x: seniority_map.get(x, x))

In [0]:
df = df.withColumn("nivel_antiguedad", seniority_udf(F.col("nivel_antiguedad")))
# df = df.fillna({
#     "Nivel_antiguedad": "Desconocido",
# })
display(df)

url title company_name company_url applications salary description nivel_antiguedad tipo_empleo funcion_laboral sectores location_clean ciudad Comunidad_Autonoma https://es.linkedin.com/jobs/view/%F0%9F%8C%8D-backend-developer-python-go-aws-100%25-remoto-%F0%9F%8C%8D-at-knowmad-mood-4295589561?position=9&pageNum=2&refId=k6gNPYI%2FL9xDzDB6w%2ByuLA%3D%3D&trackingId=vgXigtttIfXByxfH%2FwFlEw%3D%3D 🌍 Backend Developer Python - GO - AWS (100% remoto) 🌍 knowmad mood https://es.linkedin.com/company/knowmad-mood?trk=public_jobs_topcard-org-name Sé de los primeros 25 solicitantes Sin información Si tienes experiencia como Programador/a GO / Python y además cuentas con experiencia con AWS especialmente en infraestructura como código (Terraform) y quieres trabajar en una empresa del sector farmacéutico, en una modalidad 100% teletrabajo ¡esta es tu oferta!¿Qué ofrecemos?🏡 Posición 100% remota 🏡Horario flexible ⏰Vacaciones 🌴: Disfruta de 22 días de vacaciones más 2 días de libre disposición, además de los días 24 y 31 de diciembre libres = 26 días.Contrato indefinido 📄: Desde el primer día, con la opción de elegir si prefieres recibir tu nómina en 12 o 14 pagas.Retribución flexible 💳: Elige cómo destinar parte de tu salario a productos o servicios con ventajas fiscales, como tarjeta restaurante, cheque guardería, seguro médico o formación.Club de ventajas: Accede a descuentos exclusivos en tecnología, ocio y formación para mejorar tu vida personal.Formación continua 📚: Accede a plataformas como Udemy Business, además de cursos de idiomas, certificaciones oficiales y formación técnica, adaptados a tus necesidades y ritmo.Plan de carrera 🌱: Diseña tu propio camino de crecimiento, con apoyo para avanzar dentro de la empresa, transitar entre comunidades o asumir roles de liderazgo.Bienestar integral 🧘: Acceso a nuestro programa de bienestar que incluye nutrición saludable, actividad física y talleres de equilibrio emocional.Conciliación +VIDA: Asistencia personal y familiar 24/7, con servicios como consultas médicas, legales, dentales, asistencia personal, renovación de carnet de conducir y más para ti y tus familiares.Ambiente de trabajo inclusivo 🌍: Fomentamos la diversidad generacional y cultural, con políticas activas de igualdad y diversidad en un entorno de más de 70 nacionalidades.Eventos sociales y diversión 🎉: Participa en actividades como videojuegos multijugador, escape rooms virtuales y más, para conectar con tus compañeros fuera del entorno laboral.Tu misión en el proyecto:Soporte y Mejora del SistemaPlanificar, diseñar, configurar, implementar, mejorar, actualizar, probar, operar, mantener, asegurar, monitorear, liberar (gestionar cambios y comunicar a las partes interesadas) y documentar el Sistema Informático (solución SaaS + AWS), incluyendo todos sus componentes durante todo su ciclo de vida.Gestionar tareas diarias de soporte, resolución de incidencias y problemas de manera eficiente.Gestión de Infraestructura y Entornos:Apoyar en la provisión de recursos de infraestructura AWS. Diseñar, construir y desplegar configuraciones de servicios AWS usando plantillas Terraform o blueprints para servicios como S3, Lambda, IAM, MWAA, ECS, Glue y RDS.Asegurar que los entornos AWS y OpenShift sean rentables y funcionen de manera óptima. Implementar monitoreo para detectar y responder a eventos/incidencias.Configurar pipelines CI/CD para automatizar la promoción de nuevas versiones a entornos superiores.Gestión de Producto:Colaborar dentro del equipo de producto para facilitar el despliegue del sistema CPM en múltiples mercados.Participar activamente en ceremonias Scrum de gestión ágil de proyectos. Ayudar a los socios comerciales y al equipo a refinar historias de usuario. Especificar y documentar requisitos. Colaborar con equipos globales para asegurar entregas de proyectos a tiempo y dentro del alcance.Requisitos:Mínimo 3-4 años en un puesto similar.Dominio de Python y Go.Fluidez en inglés oral (obligatorio) nivel C1. Además, se tendr

Guardar en formato Delta (Plata)

In [0]:
# Nombre dinámico para el output
today = datetime.now().strftime("%Y-%m-%d")
plata_path = f"abfss://ofertas-empleo@masterhxc001sta.dfs.core.windows.net/silver/jobs_{today}/"

df.write.format("delta").mode("overwrite").save(plata_path)